In [13]:
import pandas as pd
imgatt = pd.read_csv('./input/image_attribute_labels.txt', sep='\s+', header=None, error_bad_lines=False,
warn_bad_lines=False, usecols=[0,1,2], names=['imgid','attid','present'])


C:\Users\User\AppData\Local\Temp\ipykernel_15072\2964032150.py:2: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  imgatt = pd.read_csv('./input/image_attribute_labels.txt', sep='\s+', header=None, error_bad_lines=False,
C:\Users\User\AppData\Local\Temp\ipykernel_15072\2964032150.py:2: FutureWarning: The warn_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  imgatt = pd.read_csv('./input/image_attribute_labels.txt', sep='\s+', header=None, error_bad_lines=False,


In [19]:
imgatt.head()
imgatt.shape

(3677856, 3)

In [15]:
imgatt2 = imgatt.pivot(index='imgid',columns='attid', values='present')


In [16]:
imgatt2.head()

attid  1    2    3    4    5    6    7    8    9    10   ...  303  304  305  \
imgid                                                    ...                  
1        0    0    0    0    1    0    0    0    0    0  ...    0    0    0   
2        0    0    0    0    0    0    0    0    0    0  ...    0    0    0   
3        0    0    0    0    1    0    0    0    0    0  ...    0    0    0   
4        0    0    0    0    1    0    0    0    0    0  ...    0    0    0   
5        0    0    0    0    1    0    0    0    0    0  ...    0    0    1   

attid  306  307  308  309  310  311  312  
imgid                                     
1        0    0    1    0    0    0    0  
2        0    0    0    0    0    0    0  
3        0    0    1    0    0    1    0  
4        1    0    0    1    0    0    0  
5        0    0    0    0    0    0    0  

[5 rows x 312 columns]

In [20]:
imglabels = pd.read_csv('./input/image_class_labels.txt', sep=' ', header=None, names=['imgid','label'])
imglabels = imglabels.set_index('imgid')
print(imglabels.shape)

(11788, 1)


In [37]:
df = imgatt2.join(imglabels)
df = df.sample(frac=1)
df_att = df.iloc[:, :312]
df_label = df.iloc[:, 312:]

df_att.head()
len(df_att)

11788

In [44]:
df_train_att = df_att[:8000]
df_train_label = df_label[:8000]
df_test_att = df_att[8000:]
df_test_label = df_label[8000:]

df_train_label = df_train_label['label']
df_test_label = df_test_label['label']


In [46]:
%%time

from sklearn.ensemble import RandomForestClassifier

model = RandomForestClassifier(max_features=50, random_state=0, n_estimators=100)

model.fit(df_train_att, df_train_label)

CPU times: total: 9.2 s
Wall time: 9.27 s


RandomForestClassifier(max_features=50, random_state=0)

In [54]:
y_pred= model.predict(df_train_att.head())
print(y_pred)
score = model.score(df_test_att, df_test_label)
print(score)

[ 26 109  40 185  74]
0.44904963041182683


In [59]:
from sklearn.metrics import confusion_matrix
pred_labels = model.predict(df_test_att)
cm = confusion_matrix(df_test_label, pred_labels)
print(cm)

[[ 5  2  1 ...  0  0  0]
 [ 0 14  0 ...  0  0  0]
 [ 5  0  6 ...  0  0  0]
 ...
 [ 0  0  1 ...  3  0  0]
 [ 0  0  0 ...  0  8  0]
 [ 0  0  0 ...  0  0 19]]


In [65]:
import matplotlib.pyplot as plt
import itertools
import numpy as np
def plot_confusion_matrix(cm, classes, normalize=False, title='Confusion matrix', cmap=plt.cm.Blues):
    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
    else:
        print('confusion matrix, without normarliztion')
    print(cm)

    plt.imshow(cm, cmap=cmap)
    plt.title(title)
    tick_marks = np.arange(len(classes))
    plt.xticks(tick_marks, classes, rotation=90)
    plt.yticks(tick_marks, classes)

    plt.tight_layout()
    plt.ylabel('True label')
    plt.xlabel('predicted label')


In [62]:
birds = pd.read_csv('./input/classes.txt', sep='\s+', header=None, usecols=[1], names=['birdname'])
birds = birds['birdname']
birds

0      001.Black_footed_Albatross
1            002.Laysan_Albatross
2             003.Sooty_Albatross
3           004.Groove_billed_Ani
4              005.Crested_Auklet
                  ...            
195                196.House_Wren
196                197.Marsh_Wren
197                 198.Rock_Wren
198               199.Winter_Wren
199       200.Common_Yellowthroat
Name: birdname, Length: 200, dtype: object

In [66]:
%%time

np.set_printoptions(precision=2)
plt.figure(figsize=(60,60), dpi=300)
plot_confusion_matrix(cm, classes=birds, normalize=True)
plt.show()

[[0.26 0.11 0.05 ... 0.   0.   0.  ]
 [0.   0.74 0.   ... 0.   0.   0.  ]
 [0.24 0.   0.29 ... 0.   0.   0.  ]
 ...
 [0.   0.   0.04 ... 0.13 0.   0.  ]
 [0.   0.   0.   ... 0.   0.44 0.  ]
 [0.   0.   0.   ... 0.   0.   0.86]]


CPU times: total: 52.4 s
Wall time: 53.1 s


In [67]:
from sklearn import tree
clftree = tree.DecisionTreeClassifier()
clftree.fit(df_train_att, df_train_label)
clftree.score(df_test_att, df_test_label)

0.27375923970432947

In [70]:
from sklearn.model_selection import cross_val_score
scores= cross_val_score(model, df_train_att, df_train_label, cv=5)
print(scores.mean())

0.436125
